In [3]:
import requests
import pandas as pd
from bs4 import BeautifulSoup
from tqdm import tqdm
from selenium import webdriver
from selenium.webdriver.common.by import By
from selenium.webdriver.chrome.options import Options
from selenium.webdriver.common.keys import Keys
import time

# extracting all city names

In [88]:
driver=webdriver.Chrome()
driver.get('https://www.cardekho.com/used-cars')
time.sleep(2)
driver.execute_script("window.scrollTo(0, document.body.scrollHeight);")
# scroll in the city names columns manually to the end so that all elements are loaded
time.sleep(20)
allcity=[a.text for a in driver.find_elements(By.CLASS_NAME,'gsc_col-sm-4')]
html = driver.page_source
driver.quit()

In [91]:
allcity=allcity[14:]

In [ ]:
allcity=[]
import pickle

with open('../data/raw/allcity.pkl',"wb") as f:
    allcity=pickle.dump(allcity,f)

In [98]:
len(allcity)

1584

# Extracting links of all cars

In [ ]:
import pickle
allcity=[]
with open('../data/raw/allcity.pkl',"rb") as f:
    allcity=pickle.load(f)

In [143]:
def get_car_in_city(city):
    global driver
    try:
        time.sleep(2)
        driver.find_element(By.ID,'cityName').send_keys(city+ Keys.RETURN)
        
        time.sleep(1)
        SCROLL_PAUSE_TIME = 3
        count=1
        last_height = driver.execute_script("return document.body.scrollHeight")
        while True:
            # Scroll down to bottom
            driver.execute_script("window.scrollTo(0, document.body.scrollHeight);")
            
            # Wait to load page
            time.sleep(1)
        
            # Calculate new scroll height
            new_height = driver.execute_script("return document.body.scrollHeight")
            
            if new_height == last_height:
                count+=1
            if count==10: # No more content loaded
                break;
            last_height = new_height
    
        title=driver.find_elements(By.CLASS_NAME,'title')
        cars=[i.find_element(By.TAG_NAME,'a').get_attribute('href') for i in title if i.tag_name=='h3']
        return cars
    except Exception as e:
        print(city)
        return []
    finally:
        count=0
        while True:
            try:
                time.sleep(1)
                driver.find_element(By.XPATH,f"//span[text()='{city}']").click()
                break;
            except Exception as e:
                count+=1
                if count==3:
                    break

In [5]:
def createXPath(target_classes):
    xpath_conditions = [
        f"contains(concat(' ', normalize-space(@class), ' '), ' {c} ')"
        for c in target_classes
    ]
    xpath_expression = f"//*[{' and '.join(xpath_conditions)}]"
    return xpath_expression

In [30]:
def get_all_cars():
    global driver
    try:
        # time.sleep(2)
        # driver.find_element(By.ID,'cityName').send_keys(city+ Keys.RETURN)
        
        # time.sleep(1)
        SCROLL_PAUSE_TIME = 3
        count=1
        last_height = driver.execute_script("return document.body.scrollHeight")
        target_classes=["gsc_modal","gsc_modalWindow","gsc_container","show","LocationEditScreen","gsc_thin_scroll","false"]
        pop_up=driver.find_element(By.XPATH,createXPath(target_classes))
        driver.execute_script("arguments[0].style.setProperty('display', 'none', 'important');", pop_up)
        time.sleep(3)
        while True:
            # Scroll down to bottom
            driver.execute_script("window.scrollTo(0, document.body.scrollHeight);")
            
            # Wait to load page
            time.sleep(1)
        
            # Calculate new scroll height
            new_height = driver.execute_script("return document.body.scrollHeight")
            
            if new_height == last_height:
                count+=1
            if count==10: # No more content loaded
                break;
            last_height = new_height
    
        title=driver.find_elements(By.CLASS_NAME,'title')
        cars=[i.find_element(By.TAG_NAME,'a').get_attribute('href') for i in title if i.tag_name=='h3']
        return cars
    except Exception as e:
        print(city)
        return []
    finally:
        count=0
        while True:
            try:
                time.sleep(1)
                driver.find_element(By.XPATH,f"//span[text()='{city}']").click()
                break;
            except Exception as e:
                count+=1
                if count==3:
                    break

In [31]:
all_links=[]
options = Options()
driver.set_window_size(1920, 1080)
driver=webdriver.Chrome(options=options)
driver.get(f'https://www.cardekho.com/used-cars')
time.sleep(1)
driver.execute_script("window.scrollTo(0, document.body.scrollHeight);")
time.sleep(1)
all_links+=get_all_cars()
driver.quit()

In [32]:
len(all_links)

60

In [23]:
all_links=[]
driver=webdriver.Chrome()
driver.get(f'https://www.cardekho.com/used-cars')
time.sleep(1)
driver.execute_script("window.scrollTo(0, document.body.scrollHeight);")
for city in tqdm(allcity):
    all_links+=get_car_in_city(city)
driver.quit()

NameError: name 'allcity' is not defined

In [149]:
len(all_links)

13061

In [19]:
df=pd.DataFrame(all_links,columns=['links'])

In [20]:
df.shape

(102100, 1)

In [22]:
df.duplicated().mean()*100

88.85602350636631

In [24]:
df.drop_duplicates().to_csv('../data/raw/all_links.csv',index=False)

# Extracting all cars details

In [5]:
df=pd.read_csv('../data/raw/all_links.csv')

In [17]:
opts=Options()
opts.add_argument('--headless')

In [48]:
driver=webdriver.Chrome(options=opts)
driver.get(df.values.ravel()[0])
time.sleep(1)
html = driver.page_source
driver.quit()

In [49]:
soup=BeautifulSoup(html,'html.parser')

In [50]:
box_overview=soup.find(class_='outer-card-container posR')

In [51]:
value1=[i.text for i in box_overview.find_all(class_='value-text')]
feature1=[i.text for i in box_overview.find_all(class_='label')]

In [52]:
box_specs=soup.find(class_='outer-card-container specsCard')

In [53]:
value2=[i.text for i in box_specs.find_all(class_='value-text')]
feature2=[i.text for i in box_specs.find_all(class_='label')]

In [61]:
other_features_box=soup.find(class_='outer-card-container carFeaturesContainer')
other_features=[i.text for i in other_features_box.find_all(class_='value-text')]

In [63]:
other_features

['Automatic Climate Control',
 'Parking Sensors',
 'Cooled Glovebox',
 'Cruise Control']

In [25]:
print(len(feature2),' ',len(value2))
print(len(feature1),' ',len(value1))

6   6
10   10


In [88]:
colums=['vehical_name']+feature1+feature2+['new_vehical_price','vehical_price','other_features']
car_details=pd.DataFrame(columns=colums)

In [131]:
driver=[webdriver.Chrome(options=opts) for i in range(20)]

In [99]:
failed=[]
count=0
total=df.shape[0]

In [129]:
def link(lnk):
    try:
        global driver,start_time,count,lock
        count+=1
        print(round(count*100/total,2),"% done","time-left=",round((time.time()-start_time)*(total-count)/(count*60),2),"minutes",round((time.time()-start_time)/count,2),'seconds per itr')
        thread_name = threading.current_thread().name
        worker_id = thread_name.split("_")[-1]
        time.sleep(20)
        driver[int(worker_id)].get(lnk)
        time.sleep(3)
        html = driver[int(worker_id)].page_source
        soup=BeautifulSoup(html,'html.parser')
        vehical_name=soup.find_all(class_='vehicleName')[0].text
        vehical_price=soup.find_all(class_='vehiclePrice')[0].text
        new_vehical_price=soup.find_all(class_='NcPrice')[0].text
        box_overview=soup.find(class_='outer-card-container posR')
        feature1=[]
        value1=[]
        if box_overview:
            
            feature1=[i.text for i in box_overview.find_all(class_='label')]
            value1=[i.text for i in box_overview.find_all(class_='value-text')]
        # print(len(feature1),' ',len(value1))
        box_specs=soup.find(class_='outer-card-container specsCard')
        feature2=[]
        value2=[]
        if box_specs:
            feature2=[i.text for i in box_specs.find_all(class_='label')]
            value2=[i.text for i in box_specs.find_all(class_='value-text')]
        other_features_box=soup.find(class_='outer-card-container carFeaturesContainer')
        other_features=[]
        if other_features_box:
            other_features=[i.text for i in other_features_box.find_all(class_='value-text')]
        # print(len(feature2),' ',len(value2))
        x={
            'vehical_name': vehical_name,
            **dict(zip(feature1, value1)),
            **dict(zip(feature2, value2)),
            'new_vehical_price': new_vehical_price,
            'vehical_price': vehical_price,
            'other_features':other_features
        }
        with lock:
            car_details.loc[len(car_details)] = x
    except Exception as E:
        print(E)
        print(lnk)
        failed.append(lnk)

In [102]:
# df.loc[:100,'links'].progress_apply(link)
# driver.quit()

In [ ]:
from concurrent.futures import ThreadPoolExecutor
import threading
lock = threading.Lock()
start_time=time.time()
with ThreadPoolExecutor(max_workers=20) as executor:
    executor.map(link,df['links'].values)
[driver[i].quit() for i in range(20)]

3.37 % done time-left= 0.0 minutes 0.0 seconds per itr
3.45 % done time-left= 0.01 minutes 0.0 seconds per itr
3.54 % done time-left= 0.01 minutes 0.0 seconds per itr
3.62 % done time-left= 0.01 minutes 0.0 seconds per itr
3.7 % done time-left= 0.01 minutes 0.0 seconds per itr
3.78 % done time-left= 0.01 minutes 0.0 seconds per itr
3.87 % done time-left= 0.01 minutes 0.0 seconds per itr
3.95 % done time-left= 0.01 minutes 0.0 seconds per itr
4.03 % done time-left= 0.01 minutes 0.0 seconds per itr
4.11 % done time-left= 0.01 minutes 0.0 seconds per itr
4.19 % done time-left= 0.01 minutes 0.0 seconds per itr
4.28 % done time-left= 0.01 minutes 0.0 seconds per itr
4.36 % done time-left= 0.01 minutes 0.0 seconds per itr
4.44 % done time-left= 0.01 minutes 0.0 seconds per itr
4.52 % done time-left= 0.01 minutes 0.0 seconds per itr
4.61 % done time-left= 0.01 minutes 0.0 seconds per itr
4.69 % done time-left= 0.02 minutes 0.0 seconds per itr
4.77 % done time-left= 0.01 minutes 0.0 seconds pe

In [126]:
len(failed)*100/len(df)

10.687291263842503

In [106]:
car_details.to_csv("../data/raw/car_details.csv",index=False)

In [127]:
retrieing=failed

In [128]:
count=0
failed=[]
total=len(retrieing)

In [130]:
from concurrent.futures import ThreadPoolExecutor
import threading
lock = threading.Lock()
start_time=time.time()
with ThreadPoolExecutor(max_workers=20) as executor:
    executor.map(link,retrieing[:40])
[driver[i].quit() for i in range(20)]

0.08 % done time-left= 0.02 minutes 0.0 seconds per itr
0.16 % done time-left= 0.07 minutes 0.0 seconds per itr
0.25 % done time-left= 0.05 minutes 0.0 seconds per itr
0.33 % done time-left= 0.05 minutes 0.0 seconds per itr
0.41 % done time-left= 0.04 minutes 0.0 seconds per itr
0.49 % done time-left= 0.04 minutes 0.0 seconds per itr
0.58 % done time-left= 0.05 minutes 0.0 seconds per itr
0.66 % done time-left= 0.04 minutes 0.0 seconds per itr
0.74 % done time-left= 0.04 minutes 0.0 seconds per itr
0.82 % done time-left= 0.04 minutes 0.0 seconds per itr
0.9 % done time-left= 0.04 minutes 0.0 seconds per itr
0.99 % done time-left= 0.04 minutes 0.0 seconds per itr
1.07 % done time-left= 0.03 minutes 0.0 seconds per itr
1.15 % done time-left= 0.03 minutes 0.0 seconds per itr
1.23 % done time-left= 0.03 minutes 0.0 seconds per itr
1.32 % done time-left= 0.03 minutes 0.0 seconds per itr
1.4 % done time-left= 0.03 minutes 0.0 seconds per itr
1.48 % done time-left= 0.03 minutes 0.0 seconds pe

KeyboardInterrupt: 